In [1]:
!git clone https://github.com/nateraw/huggingface-vit-finetune.git
!pip install adversarial-robustness-toolbox
!pip install timm
%cd huggingface-vit-finetune/
!pip install -r requirements.txt
!pip install git+https://github.com/huggingface/transformers.git@master --upgrade

Cloning into 'huggingface-vit-finetune'...
remote: Enumerating objects: 24, done.
remote: Counting objects: 100% (24/24), done.
remote: Compressing objects: 100% (17/17), done.
remote: Total 24 (delta 10), reused 19 (delta 6), pack-reused 0
Unpacking objects: 100% (24/24), done.
     |████████████████████████████████| 962kB 9.1MB/s 
     |████████████████████████████████| 3.2MB 32.9MB/s 
     |████████████████████████████████| 21.6MB 1.4MB/s 
     |████████████████████████████████| 235kB 54.3MB/s 
     |████████████████████████████████| 6.8MB 34.7MB/s 
     |████████████████████████████████| 25.3MB 69.5MB/s 
     |████████████████████████████████| 747kB 47.8MB/s 
  Found existing installation: llvmlite 0.34.0
    Uninstalling llvmlite-0.34.0:
      Successfully uninstalled llvmlite-0.34.0
  Found existing installation: numba 0.51.2
    Uninstalling numba-0.51.2:
      Successfully uninstalled numba-0.51.2
  Found existing installation: scikit-learn 0.22.2.post1
    Uninstalling scikit-

In [2]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torch.utils.data import DataLoader

import torchvision
import torchvision.transforms as transforms
import torchvision.datasets as datasets

import matplotlib
import matplotlib.pyplot as plt
import numpy as np

import art
from art.attacks.evasion import FastGradientMethod, ProjectedGradientDescentPyTorch
from art.estimators.classification import PyTorchClassifier

from transformers import ViTFeatureExtractor, ViTForImageClassification
import requests

import timm
from timm.data import resolve_data_config
from timm.data.transforms_factory import create_transform

In [3]:
result_dict = {}
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
device

device(type='cuda')

In [4]:
transform = transforms.Compose(
    [
      # transforms.Resize((224, 224)),
      transforms.ToTensor(),
      # transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5))
    ])
cifar_trainset = datasets.CIFAR10(root='./data', train=True, download=True, transform=transform)
cifar_testset = datasets.CIFAR10(root='./data', train=False, download=True, transform=transform)
cifar_trainloader = torch.utils.data.DataLoader(cifar_trainset, batch_size=64, shuffle=True, num_workers=2)
cifar_testloader = torch.utils.data.DataLoader(cifar_testset, batch_size=64, shuffle=False, num_workers=2)
cifar_classes = [
    'airplane', 'automobile', 'bird', 'cat', 'deer', 'dog', 'frog', 'horse', 'ship', 'truck'
]


Extracting ./data/cifar-10-python.tar.gz to ./data
Files already downloaded and verified


In [5]:
model = ViTForImageClassification.from_pretrained('nateraw/vit-base-patch16-224-cifar10', return_dict=False)
model.to(device)
model = nn.Sequential(
    nn.Upsample(scale_factor=7, mode='bilinear'),
    model
)
model

Sequential(
  (0): Upsample(scale_factor=7.0, mode=bilinear)
  (1): ViTForImageClassification(
    (vit): ViTModel(
      (embeddings): ViTEmbeddings(
        (patch_embeddings): PatchEmbeddings(
          (projection): Conv2d(3, 768, kernel_size=(16, 16), stride=(16, 16))
        )
        (dropout): Dropout(p=0.0, inplace=False)
      )
      (encoder): ViTEncoder(
        (layer): ModuleList(
          (0): ViTLayer(
            (attention): ViTAttention(
              (attention): ViTSelfAttention(
                (query): Linear(in_features=768, out_features=768, bias=True)
                (key): Linear(in_features=768, out_features=768, bias=True)
                (value): Linear(in_features=768, out_features=768, bias=True)
                (dropout): Dropout(p=0.0, inplace=False)
              )
              (output): ViTSelfOutput(
                (dense): Linear(in_features=768, out_features=768, bias=True)
                (dropout): Dropout(p=0.0, inplace=False)
             

In [6]:
# cifar-10 DATASET consists of 60000 images
correct = 0
total = 0
with torch.no_grad():
  for i, (inputs, labels) in enumerate(cifar_testloader):
    inputs, labels = inputs.to(device), labels.to(device)
    outputs = model(inputs)
    _, predicted = torch.max(outputs[0], 1)
    total += labels.size(0)
    correct += (predicted == labels).sum().item()
    if(i % 10 == 0):
      print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["Transformer"] = 100 * correct / total

/usr/local/lib/python3.7/dist-packages/torch/nn/functional.py:3458: UserWarning: Default upsampling behavior when mode=bilinear is changed to align_corners=False since 0.4.0. Please specify align_corners=True if the old behavior is desired. See the documentation of nn.Upsample for details.
  "See the documentation of nn.Upsample for details.".format(mode)


Accuracy of the network on 64 cifar-10 test images: 100.000000 %
Accuracy of the network on 704 cifar-10 test images: 99.573864 %
Accuracy of the network on 1344 cifar-10 test images: 99.330357 %
Accuracy of the network on 1984 cifar-10 test images: 99.243952 %
Accuracy of the network on 2624 cifar-10 test images: 99.161585 %
Accuracy of the network on 3264 cifar-10 test images: 99.172794 %
Accuracy of the network on 3904 cifar-10 test images: 99.103484 %
Accuracy of the network on 4544 cifar-10 test images: 99.031690 %
Accuracy of the network on 5184 cifar-10 test images: 98.900463 %
Accuracy of the network on 5824 cifar-10 test images: 98.849588 %
Accuracy of the network on 6464 cifar-10 test images: 98.855198 %
Accuracy of the network on 7104 cifar-10 test images: 98.789414 %
Accuracy of the network on 7744 cifar-10 test images: 98.747417 %
Accuracy of the network on 8384 cifar-10 test images: 98.687977 %
Accuracy of the network on 9024 cifar-10 test images: 98.736702 %
Accuracy of 

In [7]:
class Transformer(nn.Module):
  def __init__(self, model):
    super(Transformer, self).__init__()
    self.model = model
  def forward(self, x):
    return model(x)[0]

Transformer_Model = Transformer(model).to(device)
criterion = nn.CrossEntropyLoss()
optimizer = optim.Adam(model.parameters(), lr=0.01)
transformer_classifier = PyTorchClassifier(
    model=Transformer_Model.cpu(),
    loss=criterion,
    optimizer=optimizer,
    input_shape=(3, 32, 32),
    nb_classes=10,
)

In [8]:
CNN_Model = torch.hub.load("chenyaofo/pytorch-cifar-models", "cifar10_vgg16_bn", pretrained=True)
CNN_Model = CNN_Model.to(device)
criterion = nn.CrossEntropyLoss()
optimizer = optim.Adam(model.parameters(), lr=0.01)
cnn_classifier = PyTorchClassifier(
    model=CNN_Model,
    loss=criterion,
    optimizer=optimizer,
    input_shape=(3, 32, 32),
    nb_classes=10,
)

Downloading: "https://github.com/chenyaofo/pytorch-cifar-models/archive/master.zip" to /root/.cache/torch/hub/master.zip
Downloading: "https://github.com/chenyaofo/pytorch-cifar-models/releases/download/vgg/cifar10_vgg16_bn-6ee7ea24.pt" to /root/.cache/torch/hub/checkpoints/cifar10_vgg16_bn-6ee7ea24.pt


In [9]:
correct = 0
total = 0
with torch.no_grad():
  for i, (inputs, labels) in enumerate(cifar_testloader):
    inputs, labels = inputs.to(device), labels.to(device)
    outputs = CNN_Model(inputs)
    _, predicted = torch.max(outputs, 1)
    total += labels.size(0)
    correct += (predicted == labels).sum().item()
    if(i % 10 == 0):
      print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["CNN"] = 100 * correct / total

Accuracy of the network on 64 cifar-10 test images: 90.625000 %
Accuracy of the network on 704 cifar-10 test images: 94.886364 %
Accuracy of the network on 1344 cifar-10 test images: 93.898810 %
Accuracy of the network on 1984 cifar-10 test images: 93.094758 %
Accuracy of the network on 2624 cifar-10 test images: 92.492378 %
Accuracy of the network on 3264 cifar-10 test images: 92.861520 %
Accuracy of the network on 3904 cifar-10 test images: 92.622951 %
Accuracy of the network on 4544 cifar-10 test images: 92.781690 %
Accuracy of the network on 5184 cifar-10 test images: 92.689043 %
Accuracy of the network on 5824 cifar-10 test images: 92.754121 %
Accuracy of the network on 6464 cifar-10 test images: 92.821782 %
Accuracy of the network on 7104 cifar-10 test images: 92.877252 %
Accuracy of the network on 7744 cifar-10 test images: 92.884814 %
Accuracy of the network on 8384 cifar-10 test images: 92.867366 %
Accuracy of the network on 9024 cifar-10 test images: 92.752660 %
Accuracy of t

# Attack CNN model

In [11]:
eps = 0.05
attack_PGD_1_CNN = ProjectedGradientDescentPyTorch(
        estimator=cnn_classifier,
        norm="inf",
        eps=eps,
        targeted=False,
        eps_step=eps,
        max_iter=1
)

attack_PGD_1_ViT = ProjectedGradientDescentPyTorch(
        estimator=transformer_classifier,
        norm="inf",
        eps=eps,
        targeted=False,
        eps_step=eps,
        max_iter=1
)

correct = 0
total = 0
for i, (inputs, labels) in enumerate(cifar_testloader):
  inputs, labels = inputs.cpu(), labels.numpy()
  x_test_adv = attack_PGD_1_CNN.generate(x=inputs,batch_size = 64)
  outputs = transformer_classifier.predict(x_test_adv)
  predicted = np.argmax(outputs, 1)
  total += labels.size
  correct += (predicted == labels).sum().item()
  if(i % 10 == 0):
    print('Accuracy of ViT on %d cnn pgd-1 cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of ViT on %d cnn pgd-1 cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["CNN_PGD_1_on_ViT"] = 100 * correct / total

/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:670: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  x_grad = torch.tensor(x).to(self._device)
/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:671: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  y_grad = torch.tensor(y).to(self._device)
/usr/local/lib/python3.7/dist-packages/torch/nn/functional.py:3458: UserWarning: Default upsampling behavior when mode=bilinear is changed to align_corners=False since 0.4.0. Please specify align_corners=True if the old behavior is desired. See the documentation of nn.Upsample for details.
  "See the documentation of nn.Upsample for details.".forma

Accuracy of ViT on 64 cnn pgd-1 cifar-10 test images: 81.250000 %


Accuracy of ViT on 704 cnn pgd-1 cifar-10 test images: 80.823864 %


Accuracy of ViT on 1344 cnn pgd-1 cifar-10 test images: 81.473214 %


Accuracy of ViT on 1984 cnn pgd-1 cifar-10 test images: 81.552419 %


...

Accuracy of ViT on 7744 cnn pgd-1 cifar-10 test images: 79.894112 %


Accuracy of ViT on 8384 cnn pgd-1 cifar-10 test images: 79.866412 %


Accuracy of ViT on 9024 cnn pgd-1 cifar-10 test images: 79.986702 %


Accuracy of ViT on 9664 cnn pgd-1 cifar-10 test images: 79.842715 %


Accuracy of ViT on 10000 cnn pgd-1 cifar-10 test images: 79.740000 %


In [12]:
correct = 0
total = 0
for i, (inputs, labels) in enumerate(cifar_testloader):
  inputs, labels = inputs.cpu(), labels.numpy()
  x_test_adv = attack_PGD_1_ViT.generate(x=inputs,batch_size = 64)
  outputs = cnn_classifier.predict(x_test_adv)
  predicted = np.argmax(outputs, 1)
  total += labels.size
  correct += (predicted == labels).sum().item()
  if(i % 10 == 0):
    print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d pgd-1 cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["Transformer_PGD_1_on_CNN"] = 100 * correct / total

/usr/local/lib/python3.7/dist-packages/torch/nn/functional.py:3458: UserWarning: Default upsampling behavior when mode=bilinear is changed to align_corners=False since 0.4.0. Please specify align_corners=True if the old behavior is desired. See the documentation of nn.Upsample for details.
  "See the documentation of nn.Upsample for details.".format(mode)


/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:670: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  x_grad = torch.tensor(x).to(self._device)
/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:671: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  y_grad = torch.tensor(y).to(self._device)


Accuracy of the network on 64 cifar-10 test images: 53.125000 %


Accuracy of the network on 704 cifar-10 test images: 55.397727 %


Accuracy of the network on 1344 cifar-10 test images: 57.366071 %


...

Accuracy of the network on 7744 cifar-10 test images: 56.779442 %


Accuracy of the network on 8384 cifar-10 test images: 56.703244 %


Accuracy of the network on 9024 cifar-10 test images: 56.637855 %


Accuracy of the network on 9664 cifar-10 test images: 56.746689 %


Accuracy of the network on 10000 pgd-1 cifar-10 test images: 56.650000 %


In [13]:
attack_PGD_5_CNN = ProjectedGradientDescentPyTorch(
        estimator=cnn_classifier,
        norm="inf",
        eps=eps,
        targeted=False,
        eps_step=0.02,
        max_iter=5
)

attack_PGD_5_ViT = ProjectedGradientDescentPyTorch(
        estimator=transformer_classifier,
        norm="inf",
        eps=eps,
        targeted=False,
        eps_step=0.02,
        max_iter=5
)


In [14]:
correct = 0
total = 0
for i, (inputs, labels) in enumerate(cifar_testloader):
  inputs, labels = inputs.cpu(), labels.numpy()
  x_test_adv = attack_PGD_5_CNN.generate(x=inputs,batch_size = 64)
  outputs = transformer_classifier.predict(x_test_adv)
  predicted = np.argmax(outputs, 1)
  total += labels.size
  correct += (predicted == labels).sum().item()
  if(i % 10 == 0):
    print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d pgd-5 cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["CNN_PGD_5_on_ViT"] = 100 * correct / total

/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:670: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  x_grad = torch.tensor(x).to(self._device)
/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:671: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  y_grad = torch.tensor(y).to(self._device)


/usr/local/lib/python3.7/dist-packages/torch/nn/functional.py:3458: UserWarning: Default upsampling behavior when mode=bilinear is changed to align_corners=False since 0.4.0. Please specify align_corners=True if the old behavior is desired. See the documentation of nn.Upsample for details.
  "See the documentation of nn.Upsample for details.".format(mode)


Accuracy of the network on 64 cifar-10 test images: 89.062500 %


Accuracy of the network on 704 cifar-10 test images: 84.801136 %


Accuracy of the network on 1344 cifar-10 test images: 87.127976 %


...

Accuracy of the network on 7744 cifar-10 test images: 85.963326 %


Accuracy of the network on 8384 cifar-10 test images: 85.830153 %


Accuracy of the network on 9024 cifar-10 test images: 85.793440 %


Accuracy of the network on 9664 cifar-10 test images: 85.616722 %


Accuracy of the network on 10000 pgd-5 cifar-10 test images: 85.650000 %


In [15]:
correct = 0
total = 0
for i, (inputs, labels) in enumerate(cifar_testloader):
  inputs, labels = inputs.cpu(), labels.numpy()
  x_test_adv = attack_PGD_5_ViT.generate(x=inputs,batch_size = 64)
  outputs = cnn_classifier.predict(x_test_adv)
  predicted = np.argmax(outputs, 1)
  total += labels.size
  correct += (predicted == labels).sum().item()
  if(i % 10 == 0):
    print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d pgd-5 cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["Transformer_PGD_5_on_CNN"] = 100 * correct / total

/usr/local/lib/python3.7/dist-packages/torch/nn/functional.py:3458: UserWarning: Default upsampling behavior when mode=bilinear is changed to align_corners=False since 0.4.0. Please specify align_corners=True if the old behavior is desired. See the documentation of nn.Upsample for details.
  "See the documentation of nn.Upsample for details.".format(mode)


/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:670: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  x_grad = torch.tensor(x).to(self._device)
/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:671: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  y_grad = torch.tensor(y).to(self._device)


Accuracy of the network on 64 cifar-10 test images: 60.937500 %


Accuracy of the network on 704 cifar-10 test images: 61.505682 %


Accuracy of the network on 1344 cifar-10 test images: 61.904762 %


...

Accuracy of the network on 7744 cifar-10 test images: 60.653409 %


Accuracy of the network on 8384 cifar-10 test images: 60.806298 %


Accuracy of the network on 9024 cifar-10 test images: 60.671543 %


Accuracy of the network on 9664 cifar-10 test images: 60.782285 %


Accuracy of the network on 10000 pgd-5 cifar-10 test images: 60.740000 %


In [17]:
attack_PGD_10_CNN = ProjectedGradientDescentPyTorch(
        estimator=cnn_classifier,
        norm="inf",
        eps=eps,
        targeted=False,
        eps_step=0.02,
        max_iter=10
)

attack_PGD_10_ViT = ProjectedGradientDescentPyTorch(
        estimator=transformer_classifier,
        norm="inf",
        eps=eps,
        targeted=False,
        eps_step=0.02,
        max_iter=10
)


In [18]:
correct = 0
total = 0
for i, (inputs, labels) in enumerate(cifar_testloader):
  inputs, labels = inputs.cpu(), labels.numpy()
  x_test_adv = attack_PGD_10_CNN.generate(x=inputs,batch_size = 64)
  outputs = transformer_classifier.predict(x_test_adv)
  predicted = np.argmax(outputs, 1)
  total += labels.size
  correct += (predicted == labels).sum().item()
  if(i % 10 == 0):
    print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d pgd-10 cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["CNN_PGD_10_on_ViT"] = 100 * correct / total

/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:670: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  x_grad = torch.tensor(x).to(self._device)
/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:671: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  y_grad = torch.tensor(y).to(self._device)


/usr/local/lib/python3.7/dist-packages/torch/nn/functional.py:3458: UserWarning: Default upsampling behavior when mode=bilinear is changed to align_corners=False since 0.4.0. Please specify align_corners=True if the old behavior is desired. See the documentation of nn.Upsample for details.
  "See the documentation of nn.Upsample for details.".format(mode)


Accuracy of the network on 64 cifar-10 test images: 82.812500 %


Accuracy of the network on 704 cifar-10 test images: 83.380682 %


Accuracy of the network on 1344 cifar-10 test images: 84.002976 %


...

Accuracy of the network on 7744 cifar-10 test images: 83.677686 %


Accuracy of the network on 8384 cifar-10 test images: 83.587786 %


Accuracy of the network on 9024 cifar-10 test images: 83.687943 %


Accuracy of the network on 9664 cifar-10 test images: 83.567881 %


Accuracy of the network on 10000 pgd-10 cifar-10 test images: 83.500000 %


In [19]:
correct = 0
total = 0
for i, (inputs, labels) in enumerate(cifar_testloader):
  inputs, labels = inputs.cpu(), labels.numpy()
  x_test_adv = attack_PGD_10_ViT.generate(x=inputs,batch_size = 64)
  outputs = cnn_classifier.predict(x_test_adv)
  predicted = np.argmax(outputs, 1)
  total += labels.size
  correct += (predicted == labels).sum().item()
  if(i % 10 == 0):
    print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d pgd-10 cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["Transformer_PGD_10"] = 100 * correct / total

/usr/local/lib/python3.7/dist-packages/torch/nn/functional.py:3458: UserWarning: Default upsampling behavior when mode=bilinear is changed to align_corners=False since 0.4.0. Please specify align_corners=True if the old behavior is desired. See the documentation of nn.Upsample for details.
  "See the documentation of nn.Upsample for details.".format(mode)


/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:670: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  x_grad = torch.tensor(x).to(self._device)
/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:671: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  y_grad = torch.tensor(y).to(self._device)


Accuracy of the network on 64 cifar-10 test images: 62.500000 %


Accuracy of the network on 704 cifar-10 test images: 61.647727 %


Accuracy of the network on 1344 cifar-10 test images: 62.351190 %


...

Accuracy of the network on 7744 cifar-10 test images: 60.937500 %


Accuracy of the network on 8384 cifar-10 test images: 60.949427 %


Accuracy of the network on 9024 cifar-10 test images: 60.926418 %


Accuracy of the network on 9664 cifar-10 test images: 60.865066 %


Accuracy of the network on 10000 pgd-10 cifar-10 test images: 60.890000 %


In [20]:
attack_PGD_20_CNN = ProjectedGradientDescentPyTorch(
        estimator=cnn_classifier,
        norm="inf",
        eps=eps,
        targeted=False,
        eps_step=0.01,
        max_iter=20
)

attack_PGD_20_ViT = ProjectedGradientDescentPyTorch(
        estimator=transformer_classifier,
        norm="inf",
        eps=eps,
        targeted=False,
        eps_step=0.01,
        max_iter=20
)


In [21]:
correct = 0
total = 0
for i, (inputs, labels) in enumerate(cifar_testloader):
  inputs, labels = inputs.cpu(), labels.numpy()
  x_test_adv = attack_PGD_20_CNN.generate(x=inputs)
  outputs = transformer_classifier.predict(x_test_adv)
  predicted = np.argmax(outputs, 1)
  total += labels.size
  correct += (predicted == labels).sum().item()
  if(i % 10 == 0):
    print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d pgd-20 cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["CNN_PGD_20"] = 100 * correct / total

/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:670: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  x_grad = torch.tensor(x).to(self._device)
/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:671: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  y_grad = torch.tensor(y).to(self._device)


/usr/local/lib/python3.7/dist-packages/torch/nn/functional.py:3458: UserWarning: Default upsampling behavior when mode=bilinear is changed to align_corners=False since 0.4.0. Please specify align_corners=True if the old behavior is desired. See the documentation of nn.Upsample for details.
  "See the documentation of nn.Upsample for details.".format(mode)


Accuracy of the network on 64 cifar-10 test images: 84.375000 %


Accuracy of the network on 704 cifar-10 test images: 81.818182 %


Accuracy of the network on 1344 cifar-10 test images: 81.845238 %


...

Accuracy of the network on 7744 cifar-10 test images: 81.159607 %


Accuracy of the network on 8384 cifar-10 test images: 81.094943 %


Accuracy of the network on 9024 cifar-10 test images: 80.995124 %


Accuracy of the network on 9664 cifar-10 test images: 81.001656 %


Accuracy of the network on 10000 pgd-20 cifar-10 test images: 80.970000 %


In [24]:
# About 1 hour
correct = 0
total = 0
for i, (inputs, labels) in enumerate(cifar_testloader):
  inputs, labels = inputs.cpu(), labels.numpy()
  x_test_adv = attack_PGD_20_ViT.generate(x=inputs)
  outputs = cnn_classifier.predict(x_test_adv)
  predicted = np.argmax(outputs, 1)
  total += labels.size
  correct += (predicted == labels).sum().item()
  if(i % 10 == 0):
    print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d pgd-20 cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["Transformer_PGD_20"] = 100 * correct / total

/usr/local/lib/python3.7/dist-packages/torch/nn/functional.py:3458: UserWarning: Default upsampling behavior when mode=bilinear is changed to align_corners=False since 0.4.0. Please specify align_corners=True if the old behavior is desired. See the documentation of nn.Upsample for details.
  "See the documentation of nn.Upsample for details.".format(mode)


/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:670: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  x_grad = torch.tensor(x).to(self._device)
/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:671: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  y_grad = torch.tensor(y).to(self._device)


Accuracy of the network on 64 cifar-10 test images: 62.500000 %


Accuracy of the network on 704 cifar-10 test images: 62.784091 %


Accuracy of the network on 1344 cifar-10 test images: 63.541667 %


...

Accuracy of the network on 7744 cifar-10 test images: 63.429752 %


Accuracy of the network on 8384 cifar-10 test images: 63.656966 %


Accuracy of the network on 9024 cifar-10 test images: 63.707890 %


Accuracy of the network on 9664 cifar-10 test images: 63.803808 %


Accuracy of the network on 10000 pgd-20 cifar-10 test images: 63.780000 %


In [23]:
result_dict

{'CNN': 92.77,
 'CNN_PGD_10_on_ViT': 83.5,
 'CNN_PGD_1_on_ViT': 79.74,
 'CNN_PGD_20': 80.97,
 'CNN_PGD_5_on_ViT': 85.65,
 'Transformer': 98.74,
 'Transformer_PGD_10': 60.89,
 'Transformer_PGD_1_on_CNN': 56.65,
 'Transformer_PGD_5_on_CNN': 60.74}

# Results Record


